# Portfolio Optimization Project

# 📑 Table of Contents

Welcome to the **Portfolio Optimization Project** — a full walk-through of modern portfolio management concepts using Python, Jupyter, and financial theory. 

---

## Part I — Foundations: Statistics & Efficient Frontiers
- [1. Statistical Analysis & KPIs](#1-statistical-analysis--kpis)  
  Compute returns, volatility, Sharpe/Sortino ratios, skewness, kurtosis, correlations, and cumulative charts.  
- [2. Two-Asset Efficient Frontier](#2-two-asset-efficient-frontier)  
  Visualize diversification benefits with a simple two-asset trade-off.  
- [3. Three-Asset Efficient Frontier](#3-three-asset-efficient-frontier)  
  Extend frontier analysis to three assets using 3D plots.  
- [4. Multi-Asset Efficient Frontier](#4-multi-asset-efficient-frontier)  
  Construct the full frontier with all assets; compare unconstrained vs. constrained versions.  

---

## Part II — Optimization & Allocation
- [5. Mean–Variance Optimization (MVO)](#5-meanvariance-optimization-mvo)  
  Implement baseline and constrained MVO using historical mean & covariance.  
- [6. Optimal Asset Allocation](#6-optimal-asset-allocation)  
  Derive efficient allocations across risk targets and compare concentration.  
- [7. Max Sharpe & Max Sortino Portfolios](#7-maximize-sharpe--sortino-portfolios)  
  Optimize explicitly for risk-adjusted return metrics and compare results.  

---

## Part III — Forward-Looking Analysis
- [8. Capital Market Expectations](#8-capital-market-expectations)  
  Introduce forward-looking assumptions and optional Black–Litterman.  
- [9. Forward-Looking Portfolio Statistics](#9-forward-looking-portfolio-statistics)  
  Recompute risk/return metrics; simulate outcomes (Monte Carlo, VaR, CVaR).  
- [10. Strategic Asset Allocation](#10-strategic-asset-allocation)  
  Define long-term policy portfolio; compare vs. optimized allocations.  

---

## Part IV — Backtesting & Evaluation
- [11. Backtesting](#11-backtesting)  
  Run rolling-window simulations with costs, turnover, and benchmarks:  
  - Equal Weight  
  - 60/40  
  - Inverse-Volatility  
  - Min-Variance  

---

## Conclusion & Next Steps
-  Summarize insights  
-  Highlight trade-offs (theory vs. implementation)  
-  Suggest future extensions (factor models, robust optimization, Black–Litterman)  


## 📊 Statistical Analysis of Portfolio and Individual Securities

### Introduction
This notebook begins the **Portfolio Optimization Project** by analyzing the statistical properties of both the **individual securities** and the **overall portfolio**. The purpose is the following:

1. **Understand the data**: Before applying optimization techniques, we need to explore the underlying behavior of the assets in terms of returns, risk, and correlations.  
2. **Establish baselines**: These descriptive statistics will serve as benchmarks against which optimization and constraints can be evaluated.

### Objectives
- Ingest and clean price data from Financial Modeling Prep
- Compute **daily log returns** and derive annualized metrics.  
- Perform statistical analysis at both the **asset level** and **portfolio level**:  
  - Expected return  
  - Volatility (standard deviation)  
  - Sharpe ratio (with constant risk-free rate)  
  - Skewness & kurtosis  
  - Correlation matrix
  - Sortino Ratio
  - Appraisal Ratio
- Visualize key results using plots and tables.  


## STEP #1: Portfolio and Individual ETFs data analysis

In [1]:
""" 
Import all necessary modules and get fmp key

"""



import pandas as pd
import numpy as np
import os
import sys
import dotenv
from dotenv import load_dotenv

import sys
# Go one level up to the project root
parent_dir = os.path.abspath('..')
if parent_dir not in sys.path:
    sys.path.append(parent_dir)

%load_ext autoreload
%autoreload 2

import sys, os
sys.path.append(os.path.abspath('..'))  # allow importing sibling 'common/' from your notebook folder


from common.PortConnect import Port_Connect
from common.Portfolio import Portfolio_Stats

fmp_key = os.getenv("API_KEY")

port = Port_Connect(api_key=fmp_key)
portfolio = Portfolio_Stats()


#### Selecting appropiate benchmarks

SPY – SPDR S&P 500 ETF Trust - North American Large Cap Equities

EFA – iShares MSCI EAFE ETF - Developed Market ex-US Equities

EEM – iShares MSCI Emerging Markets ETF - Emerging Markets Equities

IEF – iShares 7-10 Year Treasury Bond ETF - US Treasuries (Fixed Income)

LQD – iShares iBoxx $ Investment Grade Corporate Bond ETF - US Investment Grade Corporate Bonds

VNQ – Vanguard Real Estate ETF - Real Estate (REITs)


In [2]:
spy = port.get_closing_prices('SPY',from_date='2005-01-01')
efa = port.get_closing_prices("EFA",from_date='2005-01-01')
eem = port.get_closing_prices("EEM",from_date='2005-01-01')
ief = port.get_closing_prices("IEF",from_date='2005-01-01')
lqd = port.get_closing_prices("LQD",from_date='2005-01-01')
vnq = port.get_closing_prices("VNQ",from_date='2005-01-01')

In [3]:
start_date = '2005-01-01'

spy = port.get_price_and_dividends('SPY',from_date=start_date)
efa = port.get_price_and_dividends('EFA',from_date=start_date)
eem = port.get_price_and_dividends('EEM',from_date=start_date)
ief = port.get_price_and_dividends('IEF',from_date=start_date)
lqd = port.get_price_and_dividends('LQD',from_date=start_date)
vnq = port.get_price_and_dividends('VNQ',from_date=start_date)
vti = port.get_price_and_dividends('VTI',from_date=start_date)
govt = port.get_price_and_dividends('GOVT',from_date=start_date)
tips = port.get_price_and_dividends('TIP',from_date=start_date)
mub = port.get_price_and_dividends('MUB',from_date=start_date)
conv = port.get_price_and_dividends('CWB',from_date=start_date)
blend = port.get_price_and_dividends('ACWI',from_date=start_date)
health = port.get_price_and_dividends('XLV',from_date=start_date)



#### Analyzing each security independently

In [4]:
## Create a dataframe that holds all the securitis in one

benchmark_list = [
    spy,efa,eem,ief,lqd,vnq,vti,govt,tips,mub,conv,blend,health

]

benchmark_data = []

for benchmark in benchmark_list:

    total_return = portfolio.returns_with_dividends(benchmark[benchmark.attrs['title']],benchmark['adjDividend']).to_frame(name=benchmark.attrs['title'])
    benchmark_data.append(total_return)


benchmark = pd.concat(
    benchmark_data
,axis=1)

benchmark



SPY       EFA       EEM       IEF       LQD       VNQ  \
date                                                                     
2005-01-03  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2005-01-04 -0.012219 -0.019046 -0.030644 -0.006227 -0.005612 -0.015030   
2005-01-05 -0.006901 -0.000769 -0.012087  0.001655  0.000806 -0.033243   
2005-01-06  0.005084  0.000000 -0.000941  0.000944  0.000716  0.007704   
2005-01-07 -0.001433 -0.004425  0.001884 -0.000825 -0.000447 -0.002238   
...              ...       ...       ...       ...       ...       ...   
2025-10-01  0.003407  0.008247  0.007865  0.003364  0.004001  0.001531   
2025-10-02  0.001152  0.001593  0.004645  0.001036  0.001614 -0.005242   
2025-10-03 -0.000015  0.008378  0.002959 -0.001967 -0.001253  0.003733   
2025-10-06  0.003586  0.002314  0.004610 -0.002905 -0.003227 -0.009407   
2025-10-07 -0.003708 -0.008709 -0.007709  0.002497  0.001889 -0.003644   

                 VTI      GOVT       TIP       MUB       CWB      ACWI  \
date                                                                     
2005-01-03  0.000000       NaN  0.000000       NaN       NaN       NaN   
2005-01-04 -0.013311       NaN -0.006901       NaN       NaN       NaN   
2005-01-05 -0.006918       NaN -0.001142       NaN       NaN       NaN   
2005-01-06  0.004876       NaN  0.001620       NaN       NaN       NaN   
2005-01-07 -0.003293       NaN -0.002569       NaN       NaN       NaN   
...              ...       ...       ...       ...       ...       ...   
2025-10-01  0.003474  0.001956  0.001781  0.001758  0.009952  0.005064   
2025-10-02  0.001458  0.000866 -0.000450 -0.000282  0.007337  0.002303   
2025-10-03  0.000546 -0.001298 -0.001079  0.000188  0.001413  0.001723   
2025-10-06  0.003758 -0.002165 -0.001711  0.000752  0.007056  0.003943   
2025-10-07 -0.004801  0.002170  0.002796  0.000751 -0.008731 -0.005998   

                 XLV  
date                  
2005-01-03  0.000000  
2005-01-04 -0.008043  
2005-01-05 -0.001689  
2005-01-06  0.007445  
2005-01-07 -0.000672  
...              ...  
2025-10-01  0.030897  
2025-10-02 -0.001952  
2025-10-03  0.011383  
2025-10-06 -0.004834  
2025-10-07  0.000763  

[5224 rows x 13 columns]

In [5]:
### Calculate returns from the specified ETFS
returns = benchmark

summary_list = []
names = []

### Calculate KPIS for portfolio analysis
for col in returns.columns:
    summary = portfolio.summary_stats(returns[col],market_index=returns["SPY"])
    summary_list.append(summary)
    names.append(col)
    
### Create summary of analysis for each ETF
pd.concat(summary_list,axis=0,keys=names)

Cummulative Return  Annualized Return  Annualized Vol  \
SPY  0            8.180277           0.106703        0.191097   
EFA  0            3.205877           0.057807        0.211627   
EEM  0            3.657244           0.064550        0.276817   
IEF  0            1.959762           0.032989        0.068166   
LQD  0            2.282983           0.040624        0.085695   
VNQ  0            3.915198           0.068055        0.288832   
VTI  0            8.197382           0.106814        0.193016   
GOVT 0            1.186914           0.008300        0.048489   
TIP  0            1.983276           0.033583        0.062255   
MUB  0            1.726096           0.026682        0.054261   
CWB  0            5.846620           0.088917        0.129355   
ACWI 0            3.868369           0.067436        0.203492   
XLV  0            6.867806           0.097406        0.166977   

        Annualized Semideviation  Sharpe Ratio  Skewness   Kurtosis  \
SPY  0                  0.156702      0.475267  0.001742  18.341207   
EFA  0                  0.168633      0.160095 -0.042266  17.277962   
EEM  0                  0.208539      0.160846  0.533703  21.351557   
IEF  0                  0.044261      0.065560  0.139186   5.722390   
LQD  0                  0.070879      0.145532  0.044240  62.798359   
VNQ  0                  0.235150      0.157118  0.007589  20.211435   
VTI  0                  0.157805      0.472629 -0.148388  15.582268   
GOVT 0                  0.032919     -0.335778  0.070553   8.506804   
TIP  0                  0.044348      0.078448  0.207015  12.864305   
MUB  0                  0.050287      0.011781 -1.611364  54.090994   
CWB  0                  0.106632      0.597152 -0.978173  15.494196   
ACWI 0                  0.166775      0.246598 -0.251196  14.950908   
XLV  0                  0.127629      0.512801 -0.146079  14.066314   

        Cornish-Fisher VaR (5%)  Historic CVaR (5%)  Max Drawdown  \
SPY  0                 0.015591            0.029326     -0.552014   
EFA  0                 0.017933            0.032129     -0.610452   
EEM  0                 0.019084            0.040187     -0.664488   
IEF  0                 0.006517            0.009355     -0.239245   
LQD  0                 0.002124            0.011687     -0.249610   
VNQ  0                 0.023139            0.043218     -0.730674   
VTI  0                 0.016942            0.029722     -0.554525   
GOVT 0                 0.004568            0.006729     -0.190711   
TIP  0                 0.005297            0.008831     -0.145758   
MUB  0                 0.003371            0.008054     -0.136808   
CWB  0                 0.013007            0.019613     -0.320608   
ACWI 0                 0.018502            0.031480     -0.562763   
XLV  0                 0.014959            0.024716     -0.391732   

        Drawdown Duration (Days)  Up Days %  Ulcer index  Calmar Ratio  \
SPY  0                      1772   0.551110    12.586147     -0.193297   
EFA  0                      2409   0.528905    17.702760     -0.094695   
EEM  0                      3610   0.525651    20.819316     -0.097142   
IEF  0                      1890   0.517228     7.930419     -0.137887   
LQD  0                      1476   0.533308     6.701896     -0.162749   
VNQ  0                      2044   0.530245    19.851694     -0.093141   
VTI  0                      1616   0.549579    12.426430     -0.192623   
GOVT 0                      1890   0.482336     7.316865     -0.043523   
TIP  0                      2290   0.516080     5.002984     -0.230403   
MUB  0                      1233   0.534403     3.365541     -0.195029   
CWB  0                      1614   0.546551     9.936414     -0.277338   
ACWI 0                      1754   0.539787    13.828074     -0.119830   
XLV  0                      1232   0.530436     8.997062     -0.248654   

        Sortino Ratio      Beta  Correlation  
SPY  0       0.590271  1.000000     1.000000  
EFA 

In [6]:
benchmark

SPY       EFA       EEM       IEF       LQD       VNQ  \
date                                                                     
2005-01-03  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2005-01-04 -0.012219 -0.019046 -0.030644 -0.006227 -0.005612 -0.015030   
2005-01-05 -0.006901 -0.000769 -0.012087  0.001655  0.000806 -0.033243   
2005-01-06  0.005084  0.000000 -0.000941  0.000944  0.000716  0.007704   
2005-01-07 -0.001433 -0.004425  0.001884 -0.000825 -0.000447 -0.002238   
...              ...       ...       ...       ...       ...       ...   
2025-10-01  0.003407  0.008247  0.007865  0.003364  0.004001  0.001531   
2025-10-02  0.001152  0.001593  0.004645  0.001036  0.001614 -0.005242   
2025-10-03 -0.000015  0.008378  0.002959 -0.001967 -0.001253  0.003733   
2025-10-06  0.003586  0.002314  0.004610 -0.002905 -0.003227 -0.009407   
2025-10-07 -0.003708 -0.008709 -0.007709  0.002497  0.001889 -0.003644   

                 VTI      GOVT       TIP       MUB       CWB      ACWI  \
date                                                                     
2005-01-03  0.000000       NaN  0.000000       NaN       NaN       NaN   
2005-01-04 -0.013311       NaN -0.006901       NaN       NaN       NaN   
2005-01-05 -0.006918       NaN -0.001142       NaN       NaN       NaN   
2005-01-06  0.004876       NaN  0.001620       NaN       NaN       NaN   
2005-01-07 -0.003293       NaN -0.002569       NaN       NaN       NaN   
...              ...       ...       ...       ...       ...       ...   
2025-10-01  0.003474  0.001956  0.001781  0.001758  0.009952  0.005064   
2025-10-02  0.001458  0.000866 -0.000450 -0.000282  0.007337  0.002303   
2025-10-03  0.000546 -0.001298 -0.001079  0.000188  0.001413  0.001723   
2025-10-06  0.003758 -0.002165 -0.001711  0.000752  0.007056  0.003943   
2025-10-07 -0.004801  0.002170  0.002796  0.000751 -0.008731 -0.005998   

                 XLV  
date                  
2005-01-03  0.000000  
2005-01-04 -0.008043  
2005-01-05 -0.001689  
2005-01-06  0.007445  
2005-01-07 -0.000672  
...              ...  
2025-10-01  0.030897  
2025-10-02 -0.001952  
2025-10-03  0.011383  
2025-10-06 -0.004834  
2025-10-07  0.000763  

[5224 rows x 13 columns]

#### Cummulative Return of a 100 USD investment

In [7]:
### Initial investment

initial_investment = 100

cum_return_etfs = (1 + returns.fillna(0)).cumprod() * initial_investment
cum_return_etfs

SPY         EFA         EEM         IEF         LQD  \
date                                                                     
2005-01-03  100.000000  100.000000  100.000000  100.000000  100.000000   
2005-01-04   98.778055   98.095418   96.935557   99.377350   99.438753   
2005-01-05   98.096426   98.019989   95.763858   99.541823   99.518931   
2005-01-06   98.595179   98.019989   95.673727   99.635808   99.590200   
2005-01-07   98.453865   97.586272   95.853988   99.553571   99.545657   
...                ...         ...         ...         ...         ...   
2025-10-01  817.208639  319.467805  364.100727  196.240622  228.523720   
2025-10-02  818.149997  319.976836  365.792016  196.444001  228.892605   
2025-10-03  818.137771  322.657732  366.874441  196.057580  228.605695   
2025-10-06  821.071874  323.404311  368.565731  195.488119  227.867926   
2025-10-07  818.027742  320.587673  365.724365  195.976229  228.298291   

                   VNQ         VTI        GOVT         TIP         MUB  \
date                                                                     
2005-01-03  100.000000  100.000000  100.000000  100.000000  100.000000   
2005-01-04   98.497048   98.668942  100.000000   99.309888  100.000000   
2005-01-05   95.222759   97.986348  100.000000   99.196445  100.000000   
2005-01-06   95.956343   98.464164  100.000000   99.357156  100.000000   
2005-01-07   95.741635   98.139932  100.000000   99.101910  100.000000   
...                ...         ...         ...         ...         ...   
2025-10-01  397.290821  818.967263  118.742797  198.416849  172.366565   
2025-10-02  395.208038  820.160984  118.845605  198.327649  172.317961   
2025-10-03  396.683343  820.608630  118.691393  198.113568  172.350364   
2025-10-06  392.951690  823.692409  118.434374  197.774608  172.479975   
2025-10-07  391.519777  819.738208  118.691393  198.327649  172.609586   

                   CWB        ACWI         XLV  
date                                            
2005-01-03  100.000000  100.000000  100.000000  
2005-01-04  100.000000  100.000000   99.195710  
2005-01-05  100.000000  100.000000   99.028150  
2005-01-06  100.000000  100.000000   99.765416  
2005-01-07  100.000000  100.000000   99.698391  
...                ...         ...         ...  
2025-10-01  580.592984  386.086660  683.161713  
2025-10-02  584.852700  386.975876  681.828436  
2025-10-03  585.679213  387.642789  689.590014  
2025-10-06  589.811773  389.171129  686.256821  
2025-10-07  584.661967  386.836936  686.780608  

[5224 rows x 13 columns]

In [8]:
import plotly.express as px


In [9]:
cum_return_etfs.select_dtypes('number').columns

Index(['SPY', 'EFA', 'EEM', 'IEF', 'LQD', 'VNQ', 'VTI', 'GOVT', 'TIP', 'MUB',
       'CWB', 'ACWI', 'XLV'],
      dtype='object')

In [10]:
### Create chart showing a cummulative return of different ETFs to track
numerical_columns = cum_return_etfs.select_dtypes('number').columns

fig = px.line(
    cum_return_etfs.reset_index(),
x=cum_return_etfs.index.name,
y=numerical_columns,
title='100 USD Investment on different ETFs')
fig.show()

In [11]:
historical_dividends = port.get_historical_dividends('SPY')[["symbol","adjDividend"]]
historical_dividends

symbol  adjDividend
date                          
1993-03-19    SPY      0.21300
1993-06-18    SPY      0.31800
1993-09-17    SPY      0.28600
1993-12-17    SPY      0.31700
1994-03-18    SPY      0.27100
...           ...          ...
2024-09-20    SPY      1.74553
2024-12-20    SPY      1.96555
2025-03-21    SPY      1.69553
2025-06-20    SPY      1.76112
2025-09-19    SPY      1.83111

[132 rows x 2 columns]

In [12]:
price = pd.merge(spy,historical_dividends,left_index=True,right_index=True,how='left').fillna(0)
price

SPY  adjDividend_x symbol  adjDividend_y
date                                                   
2005-01-03  120.30            0.0      0            0.0
2005-01-04  118.83            0.0      0            0.0
2005-01-05  118.01            0.0      0            0.0
2005-01-06  118.61            0.0      0            0.0
2005-01-07  118.44            0.0      0            0.0
...            ...            ...    ...            ...
2025-10-01  668.45            0.0      0            0.0
2025-10-02  669.22            0.0      0            0.0
2025-10-03  669.21            0.0      0            0.0
2025-10-06  671.61            0.0      0            0.0
2025-10-07  669.12            0.0      0            0.0

[5224 rows x 4 columns]

In [13]:
port.get_historical_dividends("SPY")

symbol             label  adjDividend  dividend  recordDate  \
date                                                                     
1993-03-19    SPY      March 19, 93      0.21300   0.21300               
1993-06-18    SPY       June 18, 93      0.31800   0.31800               
1993-09-17    SPY  September 17, 93      0.28600   0.28600               
1993-12-17    SPY   December 17, 93      0.31700   0.31700               
1994-03-18    SPY      March 18, 94      0.27100   0.27100               
...           ...               ...          ...       ...         ...   
2024-09-20    SPY  September 20, 24      1.74553   1.74553  2024-09-20   
2024-12-20    SPY   December 20, 24      1.96555   1.96555  2024-12-20   
2025-03-21    SPY      March 21, 25      1.69553   1.69553  2025-03-21   
2025-06-20    SPY       June 20, 25      1.76112   1.76112  2025-06-20   
2025-09-19    SPY  September 19, 25      1.83111   1.83111  2025-09-19   

           paymentDate declarationDate  
date                                    
1993-03-19                              
1993-06-18                              
1993-09-17                              
1993-12-17                              
1994-03-18                              
...                ...             ...  
2024-09-20  2024-10-31      2024-01-05  
2024-12-20  2025-01-31      2024-01-05  
2025-03-21  2025-04-30      2025-01-09  
2025-06-20  2025-07-31                  
2025-09-19  2025-10-31      2025-01-09  

[132 rows x 7 columns]

In [14]:
spy_w_dividends = port.get_price_and_dividends('SPY',tax=0.15,from_date='2005-01-01')
spy_w_dividends

SPY  adjDividend
date                           
2005-01-03  120.30          0.0
2005-01-04  118.83          0.0
2005-01-05  118.01          0.0
2005-01-06  118.61          0.0
2005-01-07  118.44          0.0
...            ...          ...
2025-10-01  668.45          0.0
2025-10-02  669.22          0.0
2025-10-03  669.21          0.0
2025-10-06  671.61          0.0
2025-10-07  669.12          0.0

[5224 rows x 2 columns]

In [15]:
return_with_dividend = portfolio.returns_with_dividends(spy_w_dividends['SPY'],spy_w_dividends['adjDividend'])
portfolio.annualize_rets(return_with_dividend,252)

0.10362417112561362

In [16]:
portfolio.summary_stats(return_with_dividend)

Cummulative Return  Annualized Return  Annualized Vol  \
0            7.721299           0.103624        0.191131   

   Annualized Semideviation  Sharpe Ratio  Skewness   Kurtosis  \
0                  0.156641      0.456369  0.002331  18.330392   

   Cornish-Fisher VaR (5%)  Historic CVaR (5%)  Max Drawdown  \
0                 0.015606             0.02934     -0.553941   

   Drawdown Duration (Days)  Up Days %  Ulcer index  Calmar Ratio  \
0                      1793   0.550153    12.795652     -0.187067   

   Sortino Ratio  Beta Correlation  
0       0.576798  None        None

In [17]:
### Create chart showing a cummulative return of different ETFs to track
numerical_columns = cum_return_etfs.select_dtypes('number').columns

fig = px.line(
    cum_return_etfs.reset_index(),
x=cum_return_etfs.index.name,
y=numerical_columns,
title='100 USD Investment on different ETFs')
fig.show()

### Calculate Markowitz Efficient Portfolio Theory with all given ETFS

In [18]:
returns.tail(5)

SPY       EFA       EEM       IEF       LQD       VNQ  \
date                                                                     
2025-10-01  0.003407  0.008247  0.007865  0.003364  0.004001  0.001531   
2025-10-02  0.001152  0.001593  0.004645  0.001036  0.001614 -0.005242   
2025-10-03 -0.000015  0.008378  0.002959 -0.001967 -0.001253  0.003733   
2025-10-06  0.003586  0.002314  0.004610 -0.002905 -0.003227 -0.009407   
2025-10-07 -0.003708 -0.008709 -0.007709  0.002497  0.001889 -0.003644   

                 VTI      GOVT       TIP       MUB       CWB      ACWI  \
date                                                                     
2025-10-01  0.003474  0.001956  0.001781  0.001758  0.009952  0.005064   
2025-10-02  0.001458  0.000866 -0.000450 -0.000282  0.007337  0.002303   
2025-10-03  0.000546 -0.001298 -0.001079  0.000188  0.001413  0.001723   
2025-10-06  0.003758 -0.002165 -0.001711  0.000752  0.007056  0.003943   
2025-10-07 -0.004801  0.002170  0.002796  0.000751 -0.008731 -0.005998   

                 XLV  
date                  
2025-10-01  0.030897  
2025-10-02 -0.001952  
2025-10-03  0.011383  
2025-10-06 -0.004834  
2025-10-07  0.000763

#### Calculate Covariance and Correlation Matrix

In [19]:
### Covariance Matrix
annual_cov_matrix = returns.cov() * 252
annual_cov_matrix

SPY       EFA       EEM       IEF       LQD       VNQ       VTI  \
SPY   0.036518  0.035731  0.043308 -0.003850  0.003185  0.041388  0.036634   
EFA   0.035731  0.044786  0.051015 -0.003813  0.003936  0.041928  0.036004   
EEM   0.043308  0.051015  0.076628 -0.005013  0.003989  0.052344  0.043780   
IEF  -0.003850 -0.003813 -0.005013  0.004647  0.003324 -0.002913 -0.003863   
LQD   0.003185  0.003936  0.003989  0.003324  0.007344  0.004458  0.003097   
VNQ   0.041388  0.041928  0.052344 -0.002913  0.004458  0.083424  0.042336   
VTI   0.036634  0.036004  0.043780 -0.003863  0.003097  0.042336  0.037255   
GOVT -0.001564 -0.001154 -0.001156  0.002910  0.002648  0.000395 -0.001569   
TIP  -0.001232 -0.000866 -0.001543  0.003244  0.002873 -0.000805 -0.001168   
MUB   0.001432  0.001515  0.001646  0.001471  0.002507  0.002408  0.001471   
CWB   0.018737  0.017955  0.020680 -0.001510  0.002524  0.017658  0.019576   
ACWI  0.039213  0.042581  0.049977 -0.004077  0.004240  0.045405  0.039569   
XLV   0.025798  0.025056  0.028546 -0.002434  0.002187  0.027777  0.025914   

          GOVT       TIP       MUB       CWB      ACWI       XLV  
SPY  -0.001564 -0.001232  0.001432  0.018737  0.039213  0.025798  
EFA  -0.001154 -0.000866  0.001515  0.017955  0.042581  0.025056  
EEM  -0.001156 -0.001543  0.001646  0.020680  0.049977  0.028546  
IEF   0.002910  0.003244  0.001471 -0.001510 -0.004077 -0.002434  
LQD   0.002648  0.002873  0.002507  0.002524  0.004240  0.002187  
VNQ   0.000395 -0.000805  0.002408  0.017658  0.045405  0.027777  
VTI  -0.001569 -0.001168  0.001471  0.019576  0.039569  0.025914  
GOVT  0.002351  0.002028  0.001076 -0.000600 -0.001391 -0.001094  
TIP   0.002028  0.003876  0.001320  0.000192 -0.000835 -0.000817  
MUB   0.001076  0.001320  0.002944  0.001365  0.001610  0.001323  
CWB  -0.000600  0.000192  0.001365  0.016733  0.018964  0.014040  
ACWI -0.001391 -0.000835  0.001610  0.018964  0.041409  0.027506  
XLV  -0.001094 -0.000817  0.001323  0.014040  0.027506  0.027881

In [20]:
### Correlation Matrix with visualization


# --- Compute correlation matrix ---
corr = returns.corr().round(2)

# --- Keep only the upper triangle ---
mask = np.triu(np.ones_like(corr, dtype=bool))
corr_masked = corr.where(mask)

# --- Replace NaNs with empty strings for display ---
text_matrix = corr_masked.astype(str)
text_matrix = text_matrix.mask(corr_masked.isna(), "")

# --- Plot with Plotly Express ---
fig = px.imshow(
    corr_masked,
    text_auto=True,                 # show numbers on heatmap
    color_continuous_scale="RdBu",
    zmin=-1, zmax=1,
    aspect="auto",
    labels=dict(color="Correlation"),
)

# --- Custom formatting ---
fig.update_traces(
    text=text_matrix.values,
    texttemplate="%{text}",         # display the text values
    textfont_size=12,
    hovertemplate="<b>%{y}</b> vs <b>%{x}</b><br>ρ = %{z:.2f}<extra></extra>"
)

fig.update_xaxes(side="top")
fig.update_layout(
    title="ETF Correlation Matrix (Upper Triangle)",
    coloraxis_colorbar=dict(title="ρ"),
    margin=dict(l=60, r=20, t=60, b=40)
)

fig.show()

# Optional: save to HTML
# fig.write_html("correlation_upper_triangle.html", include_plotlyjs="cdn")

In [22]:
import numpy as np
import pandas as pd
from scipy.optimize import minimize
import plotly.graph_objects as go

# -----------------------------
# 0) Inputs
# -----------------------------
# df: pandas DataFrame of periodic returns (rows=dates, cols=ETFs)
# Example assumes df already exists and is clean (numeric). If not:
# df = df.select_dtypes(include=[np.number]).dropna(how="any")

df = returns.copy()

PER_YEAR = 252            # 252 daily, 52 weekly, 12 monthly
RF = 0.00                 # annual risk-free (e.g., 0.02 for 2%)

tickers = df.columns.tolist()
n = len(tickers)
mu = df.mean().values * PER_YEAR          # annualized exp. return (shape n,)
Sigma = (df.cov().values) * PER_YEAR      # annualized covariance  (n x n)

bounds = tuple((0.0, 1.0) for _ in range(n))      # long-only
sum_to_1 = {'type': 'eq', 'fun': lambda w: np.sum(w) - 1}

def port_stats(w):
    """Return (ret, vol, sharpe) for weights w."""
    ret = w @ mu
    vol = np.sqrt(w @ Sigma @ w)
    shp = (ret - RF) / vol if vol > 0 else -np.inf
    return ret, vol, shp

# -----------------------------
# 1) Optimizers
# -----------------------------
def solve_gmv(x0=None):
    """Global Minimum-Variance portfolio, long-only."""
    if x0 is None: x0 = np.full(n, 1/n)
    obj = lambda w: w @ Sigma @ w
    res = minimize(obj, x0=x0, bounds=bounds, constraints=(sum_to_1,),
                   method="SLSQP", options={"maxiter": 1000, "ftol": 1e-12})
    w = res.x / res.x.sum()
    r, v, _ = port_stats(w)
    return w, r, v

def solve_max_sharpe(x0=None):
    """Maximize Sharpe directly (equivalent to minimizing negative Sharpe)."""
    if x0 is None: x0 = np.full(n, 1/n)
    def neg_sharpe(w):
        r, v, _ = port_stats(w)
        return -(r - RF) / v if v > 0 else 1e9
    res = minimize(neg_sharpe, x0=x0, bounds=bounds, constraints=(sum_to_1,),
                   method="SLSQP", options={"maxiter": 1000, "ftol": 1e-12})
    w = res.x / res.x.sum()
    r, v, _ = port_stats(w)
    return w, r, v

def solve_min_var_for_target(target, x0=None):
    """Min variance subject to target return and long-only."""
    if x0 is None: x0 = np.full(n, 1/n)
    ret_constraint = {'type': 'eq', 'fun': lambda w, t=target: w @ mu - t}
    obj = lambda w: w @ Sigma @ w
    res = minimize(obj, x0=x0, bounds=bounds, constraints=(sum_to_1, ret_constraint),
                   method="SLSQP", options={"maxiter": 1000, "ftol": 1e-12})
    if not res.success:
        return None
    w = res.x / res.x.sum()
    r, v, _ = port_stats(w)
    return w, r, v

# -----------------------------
# 2) Trace the efficient frontier (warm-started)
# -----------------------------
# Reasonable target range: from GMV return up to max single-asset return
w_gmv, ret_gmv, vol_gmv = solve_gmv()
ret_max_single = float(mu.max())
targets = np.linspace(ret_gmv, ret_max_single, 60)

ef_vol, ef_ret, ef_w = [], [], []
x0 = w_gmv.copy()  # warm-start from previous optimum
for t in targets:
    sol = solve_min_var_for_target(t, x0=x0)
    if sol is None: 
        continue
    w, r, v = sol
    ef_ret.append(r)
    ef_vol.append(v)
    ef_w.append(w)
    x0 = w  # warm-start next problem with the current optimum

# Max-Sharpe (good to show on the plot)
w_ms, ret_ms, vol_ms = solve_max_sharpe(x0=w_gmv)

# -----------------------------
# 3) Plot
# -----------------------------
asset_vol = np.sqrt(np.diag(Sigma))
asset_ret = mu

fig = go.Figure()

# Assets
fig.add_trace(go.Scatter(
    x=asset_vol, y=asset_ret, mode="markers+text",
    text=tickers, textposition="top center",
    name="Assets", marker=dict(size=10, symbol="circle-open"),
    hovertemplate="ETF: %{text}<br>Vol: %{x:.2%}<br>Ret: %{y:.2%}<extra></extra>"
))

# Frontier
fig.add_trace(go.Scatter(
    x=ef_vol, y=ef_ret, mode="lines+markers",
    name="Efficient Frontier",
    hovertemplate="Vol: %{x:.2%}<br>Ret: %{y:.2%}<extra></extra>"
))

# GMV & Max-Sharpe markers
fig.add_trace(go.Scatter(
    x=[vol_gmv], y=[ret_gmv], mode="markers", name="GMV",
    marker=dict(size=11, symbol="diamond"),
    hovertemplate="<b>GMV</b><br>Vol: %{x:.2%}<br>Ret: %{y:.2%}<extra></extra>"
))
fig.add_trace(go.Scatter(
    x=[vol_ms], y=[ret_ms], mode="markers", name="Max Sharpe",
    marker=dict(size=12, symbol="star"),
    hovertemplate="<b>Max Sharpe</b><br>Vol: %{x:.2%}<br>Ret: %{y:.2%}<extra></extra>"
))

fig.update_layout(
    title="Markowitz Efficient Frontier (SciPy, Long-Only)",
    xaxis_title="Annualized Volatility",
    yaxis_title="Annualized Return",
    legend=dict(x=0.02, y=0.98),
    margin=dict(l=60, r=20, t=60, b=40)
)
fig.show()

# -----------------------------
# 4) (Optional) Inspect weights
# -----------------------------
gmv_weights = pd.Series(w_gmv, index=tickers).sort_values(ascending=False)
ms_weights  = pd.Series(w_ms,  index=tickers).sort_values(ascending=False)


In [31]:
target_return = 0.09

target_solution = solve_min_var_for_target(target_return)

if target_solution is not None:
    w_opt, r_opt, v_opt = target_solution
    print("Optimal Weights:\n", pd.Series(w_opt, index=tickers).round(4))
    print(f"\nPortfolio Return: {r_opt:.2%}")
    print(f"Portfolio Volatility: {v_opt:.2%}")
    print(f"Sharpe Ratio: {(r_opt / v_opt):.2f}")
else:
    print("No feasible solution for that target (too high or too low).")

Optimal Weights:
 SPY     0.0000
EFA     0.0000
EEM     0.0000
IEF     0.3116
LQD     0.0000
VNQ     0.0000
VTI     0.0000
GOVT    0.0000
TIP     0.0000
MUB     0.0000
CWB     0.6284
ACWI    0.0000
XLV     0.0600
dtype: float64

Portfolio Return: 9.00%
Portfolio Volatility: 8.68%
Sharpe Ratio: 1.04


In [44]:
import numpy as np
import pandas as pd
from scipy.optimize import minimize
import plotly.graph_objects as go

# =========================================
# 0) INPUTS
# =========================================
# df: DataFrame of periodic returns (rows=dates, cols=ETFs)
# Ensure clean numeric data
df = df.select_dtypes(include=[np.number]).dropna(how="any")
tickers = df.columns.tolist()
n = len(tickers)

PER_YEAR   = 252      # 252 for daily, 52 weekly, 12 monthly
MAR_ANNUAL = 0   # Minimum acceptable return (annual). e.g., 0.02 for 2%

# Derived inputs
mu   = df.mean().values * PER_YEAR        # annualized exp. return (n,)
Sigma = (df.cov().values) * PER_YEAR      # annualized covariance (n x n)
R = df.values                              # T x n matrix of periodic returns
T = R.shape[0]
MAR_per = MAR_ANNUAL / PER_YEAR            # per-period MAR for downside calc

bounds = tuple((0.0, 1.0) for _ in range(n))      # long-only
sum_to_1 = {'type': 'eq', 'fun': lambda w: np.sum(w) - 1}

# =========================================
# 1) PORTFOLIO METRICS
# =========================================
def port_stats(w):
    """Return (annual_return, annual_vol, sharpe) using Sigma-based vol (not used for Sortino)."""
    r = w @ mu
    v = np.sqrt(w @ Sigma @ w)
    s = (r) / v if v > 0 else -np.inf
    return r, v, s

def downside_vol_annual(w):
    """
    Annualized downside deviation vs MAR:
    1) Portfolio per-period series: Rp_t = R @ w
    2) Downside semi-variance: mean( min(0, Rp_t - MAR_per)^2 )
    3) Semi-std (per-period), then annualize by sqrt(PER_YEAR)
    """
    Rp = R @ w                         # shape (T,)
    shortfall = np.minimum(0.0, Rp - MAR_per)
    semi_var = np.mean(shortfall**2)
    semi_std = np.sqrt(semi_var)
    return semi_std * np.sqrt(PER_YEAR)

def sortino_ratio(w):
    r_annual = w @ mu
    dvol = downside_vol_annual(w)
    if dvol <= 0:
        return -np.inf
    # Sortino relative to MAR_ANNUAL
    return (r_annual - MAR_ANNUAL) / dvol

# =========================================
# 2) SOLVERS (SciPy)
# =========================================
def solve_gmv(x0=None):
    """Global Min-Variance (long-only, classic)."""
    if x0 is None: x0 = np.full(n, 1/n)
    obj = lambda w: w @ Sigma @ w
    res = minimize(obj, x0=x0, bounds=bounds, constraints=(sum_to_1,),
                   method="SLSQP", options={"maxiter": 1000, "ftol": 1e-12})
    w = res.x / res.x.sum()
    r, v, _ = port_stats(w)
    return w, r, v

def solve_max_sortino(x0=None):
    """Maximize Sortino by minimizing its negative."""
    if x0 is None: x0 = np.full(n, 1/n)
    def neg_sortino(w):
        # Penalize out-of-bounds numerically (rare with SLSQP + bounds)
        srt = sortino_ratio(w)
        return -srt if np.isfinite(srt) else 1e9
    res = minimize(neg_sortino, x0=x0, bounds=bounds, constraints=(sum_to_1,),
                   method="SLSQP", options={"maxiter": 1000, "ftol": 1e-12})
    w = res.x / res.x.sum()
    return w, *port_stats(w)  # returns (w, ret, vol, sharpe_like)

def solve_min_var_for_target(target, x0=None):
    """Min variance subject to target **annual** return and long-only."""
    if x0 is None: x0 = np.full(n, 1/n)
    ret_constraint = {'type': 'eq', 'fun': lambda w, t=target: w @ mu - t}
    obj = lambda w: w @ Sigma @ w
    res = minimize(obj, x0=x0, bounds=bounds, constraints=(sum_to_1, ret_constraint),
                   method="SLSQP", options={"maxiter": 1000, "ftol": 1e-12})
    if not res.success:
        return None
    w = res.x / res.x.sum()
    r, v, _ = port_stats(w)
    return w, r, v

# =========================================
# 3) TRACE EFFICIENT FRONTIER (min-var for returns)
# =========================================
w_gmv, ret_gmv, vol_gmv = solve_gmv()
ret_max_single = float(mu.max())
targets = np.linspace(ret_gmv, ret_max_single, 60)

ef_vol, ef_ret, ef_w = [], [], []
x0 = w_gmv.copy()
for t in targets:
    sol = solve_min_var_for_target(t, x0=x0)
    if sol is None:
        continue
    w, r, v = sol
    ef_ret.append(r)
    ef_vol.append(v)
    ef_w.append(w)
    x0 = w  # warm start

# Best Sortino (this replaces Max-Sharpe)
w_msrt, ret_msrt, vol_msrt, _ = solve_max_sortino(x0=w_gmv)
sortino_best = sortino_ratio(w_msrt)

# =========================================
# 4) PLOT
# =========================================
asset_vol = np.sqrt(np.diag(Sigma))
asset_ret = mu

fig = go.Figure()

# Assets
fig.add_trace(go.Scatter(
    x=asset_vol, y=asset_ret, mode="markers+text",
    text=tickers, textposition="top center",
    name="Assets", marker=dict(size=10, symbol="circle-open"),
    hovertemplate="ETF: %{text}<br>Vol: %{x:.2%}<br>Ret: %{y:.2%}<extra></extra>"
))

# Frontier
fig.add_trace(go.Scatter(
    x=ef_vol, y=ef_ret, mode="lines+markers",
    name="Efficient Frontier",
    hovertemplate="Vol: %{x:.2%}<br>Ret: %{y:.2%}<extra></extra>"
))

# GMV
fig.add_trace(go.Scatter(
    x=[vol_gmv], y=[ret_gmv], mode="markers", name="GMV",
    marker=dict(size=11, symbol="diamond"),
    hovertemplate="<b>GMV</b><br>Vol: %{x:.2%}<br>Ret: %{y:.2%}<extra></extra>"
))

# Max Sortino
fig.add_trace(go.Scatter(
    x=[vol_msrt], y=[ret_msrt], mode="markers",
    name=f"Max Sortino (MAR={MAR_ANNUAL:.2%})",
    marker=dict(size=12, symbol="star"),
    hovertemplate="<b>Max Sortino</b><br>Sortino: " + f"{sortino_best:.2f}" +
                  "<br>Vol: %{x:.2%}<br>Ret: %{y:.2%}<extra></extra>"
))

fig.update_layout(
    title="Efficient Frontier (Max Sortino, SciPy, Long-Only)",
    xaxis_title="Annualized Volatility",
    yaxis_title="Annualized Return",
    legend=dict(x=0.02, y=0.98),
    margin=dict(l=60, r=20, t=60, b=40)
)
fig.show()

# =========================================
# 5) (Optional) Weights
# =========================================
gmv_weights  = pd.Series(w_gmv,   index=tickers).sort_values(ascending=False)
msrt_weights = pd.Series(w_msrt,  index=tickers).sort_values(ascending=False)


In [45]:
msrt_weights.round(2)

GOVT    0.53
SPY     0.25
XLV     0.11
MUB     0.08
IEF     0.02
CWB     0.01
EFA     0.00
ACWI    0.00
TIP     0.00
EEM     0.00
LQD     0.00
VNQ     0.00
VTI     0.00
dtype: float64